# Croisement des données 

##### *Claire Toffano-Nioche, I2BC, Paris-Saclay*

##### *Pauline Francois, Anses, Lyon*

##### *Selon les ressources de Matthias Zytnicki, INRAE, Toulouse*

##### *et toute la team Roscoff*

## Objectifs du cours

- Permettre de croiser des données génomiques de types différents
- Renforcer les notions vues précedemment
- Se familiariser avec <code>bedtools</code>

Ce que ce cours n'est pas :
- Une réponse à une vraie question biologique
- Une méthode statistiquement valide

## Croisement de données

#### Qu’est-ce c'est ?
- Une comparaison des positions ou intervalles génomiques: 
    - un variant par rapport à des gènes d’intérêt, 
    - des pics de ChIP-Seq par rapport à des gènes différentiellement exprimés, etc.
    
#### À quel moment est-ce valide ?
- Lorsque vous cherchez des co-occurrences
- Lorsque vous donnez des distributions (de distance)

#### À quel moment est-ce douteux ?
- Lorsque les résultats sont présentés comme significatifs.

#### Données disponibles
- Une liste de gènes différentiellement exprimés (Cellules avec un KO du gène beta-2-microglobulin, infectées par l'herpes simplex virus type 1 vs non infectées) (TXT)
- Une liste des sites de fixation de H3K4me3 déterminés par Chip-seq (BED)
- Une liste de variants (VCF)
- Un fichier d'annotation humain (GFF3)
- La liste des chromosomes humains et leur taille (LEN)

## Avant de commencer

Vérifier que vous êtes dans votre espace projet, sous-dossier TP_croisement

In [1]:
pwd

/shared/ifbstor1/projects/2336_nanopore/TP_croisement


## Accès aux données du TP

1. Rendez vous dans le dossier <code>data/</code> et listez en le contenu

In [2]:
cd data
ls

chrs.len  DEgenes.txt  hsGRCh38.genes.gff3  picChip.bed  variant.vcf


Ce TP repose sur 4 jeux de données, issues d'analyses précédentes ainsi que sur les annotations du génome humain : 

- la longueur des chrs (et des contigs) de la version GRCh27 du génome humain (<code>chrs.len</code>)
- une liste de SNP variants (<code>variant.vcf</code>)
- une liste des identifiants de gènes différentiellement exprimés (<code>DEgenes.txt</code>)
- une liste des pics issus d'une analyse de ChIP-seq (<code>picChip.bed</code>), ici une marque d'histone h3k4me3
- les annotations correspondant aux gènes uniquement du génome humain GRCh38 (<code>hsGRCh38.genes.gff3</code>)

2. Afin de se familiariser avec le contenu des données, on affiche les 2 premières lignes de l'ensemble des fichiers :

In [3]:
head -n 2 *

==> chrs.len <==
1	248956422
10	133797422

==> DEgenes.txt <==
ENSG00000004846
ENSG00000005981

==> hsGRCh38.genes.gff3 <==
1	ensembl_havana	gene	65419	71585	.	+	.	ID=gene:ENSG00000186092;Name=OR4F5;biotype=protein_coding;description=olfactory receptor family 4 subfamily F member 5 [Source:HGNC Symbol%3BAcc:HGNC:14825];gene_id=ENSG00000186092;logic_name=ensembl_havana_gene;version=6
1	ensembl_havana	gene	450703	451697	.	-	.	ID=gene:ENSG00000284733;Name=OR4F29;biotype=protein_coding;description=olfactory receptor family 4 subfamily F member 29 [Source:HGNC Symbol%3BAcc:HGNC:31275];gene_id=ENSG00000284733;logic_name=ensembl_havana_gene;version=1

==> picChip.bed <==
22	16192349	16192565	region_1
22	16846630	16870710	region_2

==> variant.vcf <==
##fileformat=VCFv4.0
##fileDate=20180418


3. Pour le fichier variant.vcf on ne voit que des commentaires (souvent des lignes qui commencent par "#") ; afficher les deux dernières lignes de ce fichier :

In [4]:
tail -n 2 variant.vcf

Y	26614668	rs376925794	TC	T	.	.	RS=376925794;RSPOS=26614671;dbSNPBuildID=138;SSR=0;SAO=0;VP=0x050000000005000002000200;WGT=1;VC=DIV;ASP;CAF=0.9968,0.003244;COMMON=1
Y	26624486	rs771929773	T	TA	.	.	RS=771929773;RSPOS=26624486;dbSNPBuildID=144;SSR=0;SAO=0;VP=0x050000000005040024000200;WGT=1;VC=DIV;ASP;VLD;KGPhase3;CAF=0.9968,0.003244;COMMON=1


4. Activer les outils bedtools (v2.30.0) et bc (1.07.1) dont nous aurons besoin plus loin

In [5]:
module load bedtools/2.30.0 bc/1.07.1

## Problème

##### *Question scientifique*

Mes gènes différentiellement exprimés contiennent-ils plus de pics de chip qu'attendu ? (oui/non, pas de quantification)

En d'autres termes, y a-t-il plus ou moins de pics de chip-seq dans les gènes différentiellement exprimés par rapport aux gènes non différentiellement exprimés ?

##### *Données*
- DEgenes.txt
- picChip.bed
- hsGRCh38.genes.gff3

Afficher les cinq premières lignes des fichiers <code>DEgenes.txt</code>, <code>picChip.bed</code> et <code>hsGRCh38.genes.gff3</code> :

In [6]:
head -n 5 DEgenes.txt picChip.bed hsGRCh38.genes.gff3

==> DEgenes.txt <==
ENSG00000004846
ENSG00000005981
ENSG00000006747
ENSG00000015568
ENSG00000047457

==> picChip.bed <==
22	16192349	16192565	region_1
22	16846630	16870710	region_2
22	17067019	17067283	region_3
22	17070620	17114004	region_4
22	17128021	17136091	region_5

==> hsGRCh38.genes.gff3 <==
1	ensembl_havana	gene	65419	71585	.	+	.	ID=gene:ENSG00000186092;Name=OR4F5;biotype=protein_coding;description=olfactory receptor family 4 subfamily F member 5 [Source:HGNC Symbol%3BAcc:HGNC:14825];gene_id=ENSG00000186092;logic_name=ensembl_havana_gene;version=6
1	ensembl_havana	gene	450703	451697	.	-	.	ID=gene:ENSG00000284733;Name=OR4F29;biotype=protein_coding;description=olfactory receptor family 4 subfamily F member 29 [Source:HGNC Symbol%3BAcc:HGNC:31275];gene_id=ENSG00000284733;logic_name=ensembl_havana_gene;version=1
1	ensembl_havana	gene	685679	686673	.	-	.	ID=gene:ENSG00000284662;Name=OR4F16;biotype=protein_coding;description=olfactory receptor family 4 subfamily F member 16 [Source:H

<code>DEgenes.txt</code> est notre liste de gènes DE :

![](images/liste_geneDE.png)

.

.

<code>picChip.bed</code> est notre liste de pics issus du chip-seq et positionnés sur le génome :

![](images/liste_chip.png)

.

.

Pour croiser ces données il faut positionner les gènes DE sur le génome, on fait cela grâce au fichier d'annotation (gènes non DE plus clairs) :

![](images/genes_position_genome.png)

.

.

Le positionnement des données sur le génome permet maintenant de les croiser :

![](images/associationGeneDE_chip.png)

.

.

Le but sera de compter le nombre gène dans chacune des 4 classes possibles :

![](images/geneDE_Chip.png)

##### *Protocole envisagé*
<details><summary></summary>

  A. Extraire les intervalles génomiques des gènes différentiellement exprimés (DE)
    
  B. Comparer les intervalles génomiques des gènes DE avec les régions H3K4me3 (ie. l'emplacement des pics de chip-seq)
  
  C. Compter le nombre de chevauchements entre les gènes DE et les pics

  D. Trouver les intervalles génomiques des gènes non-différentiellement exprimés

  E. Comparer ces intervalles génomiques avec les régions H3K4me3

  F. Compter le nombre de chevauchements entre les gènes non DE et les pics

  G. Comparer les nombres de chevauchements

</details>

.

.

.

#### A. Extraire les intervalles génomiques des gènes différentiellement exprimés (DE)

1. Chercher (<code>grep</code>) une liste de mots (<code>-f</code>) contenue dans le fichier DEgenes.txt dans le fichier <code>hsGRCh38.genes.gff3</code> et rediriger la sortie standard dans un fichier nommé <code>DEgenes.gff3</code>

In [7]:
grep -f DEgenes.txt hsGRCh38.genes.gff3 > DEgenes.gff3
wc -l DEgenes.txt
wc -l DEgenes.gff3
wc -l hsGRCh38.genes.gff3
head DEgenes.gff3

162 DEgenes.txt
162 DEgenes.gff3
21492 hsGRCh38.genes.gff3
1	ensembl_havana	gene	33081104	33120530	.	+	.	ID=gene:ENSG00000142920;Name=AZIN2;biotype=protein_coding;description=antizyme inhibitor 2 [Source:HGNC Symbol%3BAcc:HGNC:29957];gene_id=ENSG00000142920;logic_name=ensembl_havana_gene;version=16
1	ensembl_havana	gene	70852353	71047808	.	-	.	ID=gene:ENSG00000050628;Name=PTGER3;biotype=protein_coding;description=prostaglandin E receptor 3 [Source:HGNC Symbol%3BAcc:HGNC:9595];gene_id=ENSG00000050628;logic_name=ensembl_havana_gene;version=20
1	ensembl_havana	gene	74198235	74544393	.	+	.	ID=gene:ENSG00000259030;Name=FPGT-TNNI3K;biotype=protein_coding;description=FPGT-TNNI3K readthrough [Source:HGNC Symbol%3BAcc:HGNC:42952];gene_id=ENSG00000259030;logic_name=ensembl_havana_gene;version=7
1	ensembl_havana	gene	111722064	111755824	.	-	.	ID=gene:ENSG00000284755;Name=AL049557.1;biotype=protein_coding;description=inka box actin regulator 2 [Source:NCBI gene%3BAcc:55924];gene_id=ENSG00000284755

.


#### B. Comparer les intervalles génomiques des gènes DE avec les régions H3K4me3 (ie. l'emplacement des pics de chip-seq)

Comme on va utiliser la suite d'outils que propose [Bedtools](https://bedtools.readthedocs.io/en/latest/content/bedtools-suite.html), avant tout, faisons un tour sur la documentation.

Chaque sous-commande fonctionne sur le même principe :

<code>bedtools [sub-command] [options]</code>

Les options varient selon la commande. Il suffit de cliquer sur son nom sur le site pour avoir accès à la fonction de la commande, à ses options et à des exemples.

Les trois qui nous intéresserons dans un premier temps sont [<code>intersect</code>](https://bedtools.readthedocs.io/en/latest/content/tools/intersect.html), [<code>flank</code>](https://bedtools.readthedocs.io/en/latest/content/tools/flank.html) et [<code>closest</code>](https://bedtools.readthedocs.io/en/latest/content/tools/closest.html)

Bedtools accepte quasiment tous les formats de fichiers tabulés (GFF3, BED, etc)

Dans notre cas de figure, nous souhaitons savoir si des gènes DE contiennent des pics et obtenir le nom de ces gènes. Nous utilisons donc la sous-commande "bedtools ....." ?

Le fichier A sera celui de l'annotation des gènes DE (<code>DEgenes.gff3</code>) et le B correspondra aux pics (<code>picChip.bed</code>). Quelle option choisir pour obtenir uniquement les annotations du fichier A qui croisent avec le fichier B ?

Rediriger la sortie standard dans un fichier nommé <code>intersect_DEgenes_picChip.gff3</code>

In [8]:
bedtools intersect -a DEgenes.gff3 -b picChip.bed -wa  -u > intersect_DEgenes_picChip.gff3

.

#### C. Compter le nombre de chevauchements entre les gènes DE et les pics

Nous avons obtenu la liste des gènes dans lesquels se trouvent des pics (<code>intersect_DEgenes_picChip.gff3</code>). Nous avons maintenant besoin de les compter.

In [9]:
wc -l intersect_DEgenes_picChip.gff3

77 intersect_DEgenes_picChip.gff3


.


#### D. Trouver les intervalles génomiques des gènes non-différentiellement exprimés

grep -v : Chercher l'inverse d'une liste de gènes dans un texte et rediriger la sortie standard dans un fichier nommé <code>notDEgenes.gff3</code>

On récupère donc tous les gènes dont le nom n'est pas dans la liste des gènes DE.

In [10]:
grep -v -f DEgenes.txt hsGRCh38.genes.gff3 > notDEgenes.gff3
wc -l notDEgenes.gff3

21330 notDEgenes.gff3


#### E.  Comparer ces intervalles génomiques avec les régions H3K4me3
Faire l'intersection entre le fichier gff3 des gènes non DE et les pics de Chip-seq et écrire la sortie dans un fichier <code>intersect_notDEgenes_picChip.gff3</code>

In [11]:
bedtools intersect -a notDEgenes.gff3 -b picChip.bed -wa -u > intersect_notDEgenes_picChip.gff3
wc -l intersect_notDEgenes_picChip.gff3

9438 intersect_notDEgenes_picChip.gff3


.


#### F. Compter le nombre de chevauchements entre les gènes non DE et les pics

Afin de pouvoir ensuite faire des ratios "nb de gène avec au moins un chevauchements/nb de gène" nous devons connaitre les valeurs suivantes :
- Nombre de gènes DE
- Nombre de gènes DE avec chevauchement
- Nombre de gènes non DE
- Nombre de gènes non DE avec chevauchement


In [12]:
wc -l DEgenes.gff3
wc -l intersect_DEgenes_picChip.gff3
wc -l notDEgenes.gff3
wc -l intersect_notDEgenes_picChip.gff3

162 DEgenes.gff3
77 intersect_DEgenes_picChip.gff3
21330 notDEgenes.gff3
9438 intersect_notDEgenes_picChip.gff3


.

#### G. Comparer les nombres de chevauchements

Résumons nos informations :
 
 Ratios | avec pics | sans pic | total
-----------|----------|----------|-------
gene DE    |77        |162-77    |162
gene non DE|9438      |21330-9438|21330    
total      |          |          |21492

Par simple calcul de pourcentage nous obtenons le tableau suivant :

Ratios | avec pics | sans pic | total
-----------|----------|----------|-------
gene DE    |47.53%        | 52.47%    |162
gene non DE|44.24%      |55.76%|21330    
total      |          |          |21492

En conclusion : 
On peut noter une légère hausse du nombre de pics dans les gènes DE vs non DE.

/!\ En revanche on ne peut pas affirmer ou infirmer que cela soit significatif /!\

.

.

.

## Bonus n°1

##### *Question scientifique*

Quels sont les variants qui sont dans les promoteurs (2kb en amont du gène) des gènes différentiellement exprimés ?

##### *Données*
- DEgenes.gff3 (généré précédemment)
- variant.vcf
- chrs.len

Afficher les cinq dernières lignes des fichiers <code>DEgenes.gff3</code> et <code>variant.vcf</code> :

In [14]:
tail -n5 DEgenes.gff3 variant.vcf

==> DEgenes.gff3 <==
9	ensembl_havana	gene	127738317	127778741	.	-	.	ID=gene:ENSG00000095370;Name=SH2D3C;biotype=protein_coding;description=SH2 domain containing 3C [Source:HGNC Symbol%3BAcc:HGNC:16884];gene_id=ENSG00000095370;logic_name=ensembl_havana_gene;version=19
9	ensembl_havana	gene	128149071	128153455	.	+	.	ID=gene:ENSG00000148346;Name=LCN2;biotype=protein_coding;description=lipocalin 2 [Source:HGNC Symbol%3BAcc:HGNC:6526];gene_id=ENSG00000148346;logic_name=ensembl_havana_gene;version=11
9	ensembl_havana	gene	132725578	132878777	.	-	.	ID=gene:ENSG00000165695;Name=AK8;biotype=protein_coding;description=adenylate kinase 8 [Source:HGNC Symbol%3BAcc:HGNC:26526];gene_id=ENSG00000165695;logic_name=ensembl_havana_gene;version=9
9	havana	gene	133098121	133163914	.	-	.	ID=gene:ENSG00000285245;Name=AL162417.1;biotype=protein_coding;description=novel protein;gene_id=ENSG00000285245;logic_name=havana;version=1
X	ensembl_havana	gene	71107404	71112108	.	-	.	ID=gene:ENSG00000147168;Name=IL2RG

##### *Protocole envisagé*
<details><summary></summary>

  A. Extraire la région située à 2kb en amont des gènes différentiellement exprimés (DE)
    
  B. Trouver tous les variants chevauchant les régions trouvées précedemment

</details>

.



Nous allons avoir besoin d'une autre sous-commande de bedtools : [<code>bedtools flank</code>](https://bedtools.readthedocs.io/en/latest/content/tools/flank.html) Regardez bien ses options.

Notons qu'il y a une option obligatoire, <code>-g</code> pour communiquer à l'outil la taille des chromosomes. Pourquoi ?

Lancer la commande et écrire la sortie standard dans un fichier <code>flank2kDEgenes.gff3</code>

In [15]:
bedtools flank -i DEgenes.gff3 -g chrs.len -l 2000 -r 0 -s > flank2kDEgenes.gff3
head -n5 flank2kDEgenes.gff3

1	ensembl_havana	gene	33079104	33081103	.	+	.	ID=gene:ENSG00000142920;Name=AZIN2;biotype=protein_coding;description=antizyme inhibitor 2 [Source:HGNC Symbol%3BAcc:HGNC:29957];gene_id=ENSG00000142920;logic_name=ensembl_havana_gene;version=16
1	ensembl_havana	gene	71047809	71049808	.	-	.	ID=gene:ENSG00000050628;Name=PTGER3;biotype=protein_coding;description=prostaglandin E receptor 3 [Source:HGNC Symbol%3BAcc:HGNC:9595];gene_id=ENSG00000050628;logic_name=ensembl_havana_gene;version=20
1	ensembl_havana	gene	74196235	74198234	.	+	.	ID=gene:ENSG00000259030;Name=FPGT-TNNI3K;biotype=protein_coding;description=FPGT-TNNI3K readthrough [Source:HGNC Symbol%3BAcc:HGNC:42952];gene_id=ENSG00000259030;logic_name=ensembl_havana_gene;version=7
1	ensembl_havana	gene	111755825	111757824	.	-	.	ID=gene:ENSG00000284755;Name=AL049557.1;biotype=protein_coding;description=inka box actin regulator 2 [Source:NCBI gene%3BAcc:55924];gene_id=ENSG00000284755;logic_name=ensembl_havana_gene;version=1
1	ensembl_havana	

Maintenant, c'est du déjà-vu : Trouver tous les variants chevauchant les régions trouvées précedemment. Renvoyer la sortie standard dans un fichier nommé <code>intersect_flank2kDEgenes_variant.txt</code>

N'oubliez pas de regarder les options qui nous intéressent [ici](https://bedtools.readthedocs.io/en/latest/content/tools/intersect.html) et visualisez les 5 premières lignes du fichier quand celui ci est généré

In [16]:
bedtools intersect -a variant.vcf -b flank2kDEgenes.gff3 -wa -u > intersect_flank2kDEgenes_variant.txt
head -n 5 intersect_flank2kDEgenes_variant.txt
wc -l intersect_flank2kDEgenes_variant.txt

1	33079702	rs10712676	GA	G	.	.	RS=10712676;RSPOS=33079703;dbSNPBuildID=137;SSR=0;SAO=0;VP=0x0501000a0005170126000200;GENEINFO=AZIN2:113451|LOC105378635:105378635;WGT=1;VC=DIV;SLO;INT;R5;ASP;VLD;G5A;G5;GNO;KGPhase3;CAF=0.8706,0.1294;COMMON=1;TOPMED=0.96872610856269113,0.03127389143730886
1	74197393	rs201749320	TTC	T	.	.	RS=201749320;RSPOS=74197394;dbSNPBuildID=137;SSR=0;SAO=0;VP=0x0500000a000504003e000200;GENEINFO=LRRIQ3:127255|FPGT-TNNI3K:100526835|FPGT:8790;WGT=1;VC=DIV;INT;R5;ASP;VLD;KGPhase1;KGPhase3;CAF=0.9958,0.004193;COMMON=1;TOPMED=0.99698967889908256,0.00301032110091743
1	147773875	rs72546659	C	CT	.	.	RS=72546659;RSPOS=147773875;dbSNPBuildID=130;SSR=0;SAO=0;VP=0x0501100a000504003e000200;GENEINFO=GJA5:2702|LOC102723321:102723321;WGT=1;VC=DIV;TPA;SLO;INT;R5;ASP;VLD;KGPhase1;KGPhase3;CAF=0.9968,0.003195;COMMON=1;TOPMED=0.99143890163098878,0.00856109836901121
1	147775166	rs10641806	A	AAT	.	.	RS=10641806;RSPOS=147775166;dbSNPBuildID=135;SSR=0;SAO=0;VP=0x0500000a000515003e000200;GENE

Pour aller plus loin avec bedtools <code>intersect</code>, on peut se demander combien y a-t-il de SNP par promoteur ? 

Stocker l'information dans un fichier <code>intersect_flanck2kDEgenes_n_variant.txt</code> et visualiser les 5 premières lignes

In [17]:
bedtools intersect -a flank2kDEgenes.gff3 -b variant.vcf -c > intersect_flanck2kDEgenes_n_variant.txt
head -n 5 intersect_flanck2kDEgenes_n_variant.txt

1	ensembl_havana	gene	33079104	33081103	.	+	.	ID=gene:ENSG00000142920;Name=AZIN2;biotype=protein_coding;description=antizyme inhibitor 2 [Source:HGNC Symbol%3BAcc:HGNC:29957];gene_id=ENSG00000142920;logic_name=ensembl_havana_gene;version=16	1
1	ensembl_havana	gene	71047809	71049808	.	-	.	ID=gene:ENSG00000050628;Name=PTGER3;biotype=protein_coding;description=prostaglandin E receptor 3 [Source:HGNC Symbol%3BAcc:HGNC:9595];gene_id=ENSG00000050628;logic_name=ensembl_havana_gene;version=20	0
1	ensembl_havana	gene	74196235	74198234	.	+	.	ID=gene:ENSG00000259030;Name=FPGT-TNNI3K;biotype=protein_coding;description=FPGT-TNNI3K readthrough [Source:HGNC Symbol%3BAcc:HGNC:42952];gene_id=ENSG00000259030;logic_name=ensembl_havana_gene;version=7	1
1	ensembl_havana	gene	111755825	111757824	.	-	.	ID=gene:ENSG00000284755;Name=AL049557.1;biotype=protein_coding;description=inka box actin regulator 2 [Source:NCBI gene%3BAcc:55924];gene_id=ENSG00000284755;logic_name=ensembl_havana_gene;version=1	0
1	ensembl

.

.

.

## Bonus n°2

##### *Question scientifique*

Quels sont les gènes différentiellement exprimés les plus proches des pics ChIP ET qui contiennent une mutation ?

##### *Données*
- DEgenes.gff3 (généré dans le problème 1)
- variant.vcf
- picChip.bed

Afficher les cinq dernières lignes des fichiers <code>DEgenes.gff3</code>, <code>variant.vcf</code> et <code>picChip.bed</code> :

In [18]:
tail -n5 DEgenes.gff3 variant.vcf picChip.bed

==> DEgenes.gff3 <==
9	ensembl_havana	gene	127738317	127778741	.	-	.	ID=gene:ENSG00000095370;Name=SH2D3C;biotype=protein_coding;description=SH2 domain containing 3C [Source:HGNC Symbol%3BAcc:HGNC:16884];gene_id=ENSG00000095370;logic_name=ensembl_havana_gene;version=19
9	ensembl_havana	gene	128149071	128153455	.	+	.	ID=gene:ENSG00000148346;Name=LCN2;biotype=protein_coding;description=lipocalin 2 [Source:HGNC Symbol%3BAcc:HGNC:6526];gene_id=ENSG00000148346;logic_name=ensembl_havana_gene;version=11
9	ensembl_havana	gene	132725578	132878777	.	-	.	ID=gene:ENSG00000165695;Name=AK8;biotype=protein_coding;description=adenylate kinase 8 [Source:HGNC Symbol%3BAcc:HGNC:26526];gene_id=ENSG00000165695;logic_name=ensembl_havana_gene;version=9
9	havana	gene	133098121	133163914	.	-	.	ID=gene:ENSG00000285245;Name=AL162417.1;biotype=protein_coding;description=novel protein;gene_id=ENSG00000285245;logic_name=havana;version=1
X	ensembl_havana	gene	71107404	71112108	.	-	.	ID=gene:ENSG00000147168;Name=IL2RG

##### *Protocole envisagé*
<details><summary></summary>

  1. Trouver les pics qui contiennent une mutation
    
  2. Trouver le gène le plus proche de chaque région précédemment trouvée

</details>

.

.

.

#### Trouver les pics qui contiennent une mutation

Rien de neuf sous le soleil, nous stockons l'output dans un fichier <code>picVariant.bed</code>.

In [19]:
bedtools intersect -a picChip.bed -b variant.vcf -u > picVariant.bed

## L'option -u permet de garder l'ensemble de l'information des pics sans ajouter celle des variants
head -n 5 picVariant.bed

22	16846630	16870710	region_2
22	17070620	17114004	region_4
22	17128021	17136091	region_5
22	17147545	17173488	region_6
22	17192673	17206732	region_7


.

#### Trouver le gène le plus proche de chaque région précédemment trouvée

Nous avons besoin d'une nouvelle sous-commande : [<code>bedtools closest</code>](https://bedtools.readthedocs.io/en/latest/content/tools/closest.html)

Attention, bien prendre note du message suivant :
![](images/exo3_graph1.png)

L'output est à stocker dans un fichier nommé <code>picVariant_sorted.bed</code>

In [20]:
sort -k1,1 -k2,2n picVariant.bed > picVariant_sorted.bed

Nous tentons un essai en paramètre par défaut. Rediriger la sortie dans un fichier <code>DEgenes_closest_picVariant.bed</code>

In [21]:
bedtools closest -a picVariant_sorted.bed -b DEgenes.gff3 > DEgenes_closest_picVariant.bed

Et si on prenait en compte le brin ?

In [22]:
bedtools closest -a picVariant_sorted.bed -b DEgenes.gff3 -s > DEgenes_closest_picVariant.bed

Afficher le nombre de ligne

In [23]:
wc -l DEgenes_closest_picVariant.bed

28080 DEgenes_closest_picVariant.bed


.

.

.

## Bonus n°3

#### *Devine la commande*

Ce dernier bonus est l'occasion de voir des commandes qui peuvent être utiles mais que nous n'avons pas pu aborder précédemment 

#### *Awk*

1. Pour commencer, un peu de Awk. Vous trouverez un fichier nommé .DEgenes_all.gff3 (ls -la pour le voir). Récuperez uniquement les annotations de gènes

In [24]:
awk 'BEGIN {OFS=FS="\t"} $3 == "gene" {print}' ".DEgenes_all.gff3" > DEgenes.gff3 

- <code>FS</code> et <code>OFS</code> : Permettrent de définir le séparateur de champ du fichier
- <code>$3 == "gene"</code> : Permet de vérifier si la colonne 3 est une annotation de gène
- <code>print</code> : Imprime à l'écran la ligne quand la condition est vraie

2. La dernière colonne du fichier intersect_flanck2kDEgenes_n_variant.txt contient le nombre de variants par promoteur. Comment s'assurer que nous avons bien pris en compte les 405 variants initialement trouvé à la question bonus 1 ?

In [25]:
awk -F '\t' 'BEGIN{s=0}{s+=$NF}END{print s}' intersect_flanck2kDEgenes_n_variant.txt

405


- <code>-F</code> : Permet de définir le séparateur de champ dans l'input
- <code>s=0</code> : Initialisation d'une variable s qui vaut 0 avant de lire le fichier
- <code>s+=$NF</code> : Pour chaque ligne, on ajoute la valeur de la dernière colonne à la somme s
- <code>print s</code> : Une fois l'ensemble du fichier parcouru, on imprime la dernière valeur de la somme s

#### *Alternative à grep -v*

Dans l'exercice, point D, on utilise <code>grep -v</code> pour extraire les coordonnées génomiques des gènes non DE.

Il était aussi possible de le faire avec la commande <code>intersect</code>.

Trouverez vous comment ?

Attention aux options !

In [26]:
bedtools intersect -a hsGRCh38.genes.gff3 -b DEgenes.gff3 -v -f 1 -F 1 -s -wa > notDEgenes.gff3
wc -l notDEgenes.gff3

21330 notDEgenes.gff3


L'option la plus importante pour cette question est donc l'option <code>-v</code>. 

Mais par défaut, <code>intersect</code> valide une intersection dès qu'il y a une base en commun entre les 2 régions. Dans ce cas d'usage où l'on traite des gènes en entier, il suffit que quelques gènes se chevauchent pour qu'ils soient exclus à tort. La façon correcte est donc de préciser que l'on veut valider les chevauchements que si les gènes se chevauchent à 100% entre eux. Les options pour spécifier un % de chavauchement (exprimés entre <code>[0-1]</code>, 1 pour 100%) sont <code>-F</code> pour le fichier A et <code>-f</code> pour le fichier B. Il faut aussi que les 2 gènes soient sur le même brin (option <code>-s</code>).